# Word embeddings

In [1]:
!pip install -U gensim
!pip install -U "datasets<3.0"

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 27.9/27.9 MB 42.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 527.3/527.3 kB 12.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 177.6/177.6 kB 14.2 MB/s eta 0:00:00
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2025.3.0
    Uninstalling fsspec-2025.3.0:
      Successfully uninstalled fsspec-2025.3.0
  Attempting uninstall: datasets
    Found existing installation: datasets 4.0.0
    Uninstalling datasets-4.0.0:
      Successfully uninstalled datasets-4.0.0
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gcsfs 2025.3.0 requires fsspec==2025.3.0, but you have fsspec 2024.6.1 which is incompatible.


In [2]:
import datasets # Biblioteca de manejo de conjuntos de datos para procesamiento de lenguaje natural
import re
import gensim # Biblioteca de modelamiento de lenguaje
import numpy as np # Biblioteca de manejo de datos vectoriales
import sklearn.linear_model # Módulo de sklearn de modelamiento lineal
import sklearn.decomposition # Módulo de sklearn donde está PCA
import plotly.express as px # Biblioteca de visualización
import urllib # Módulo de python para el manejo de consultas web

Cargamos el conjunto de datos del curso.

In [3]:
spanish_diagnostics = datasets.load_dataset('fvillena/spanish_diagnostics') # Cargamos las particiones de entrenamiento y prueba

/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:104: UserWarning: 
Error while fetching `HF_TOKEN` secret value from your vault: 'Requesting secret HF_TOKEN timed out. Secrets can only be fetched when running from the Colab UI.'.
You are not authenticated with the Hugging Face Hub in this notebook.
If the error persists, please let us know by opening an issue on GitHub (https://github.com/huggingface/huggingface_hub/issues/new).
  warnings.warn(


Generating train split:   0%|          | 0/70000 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/30000 [00:00<?, ? examples/s]

Preprocesamos el corpus.

In [4]:
#Reutilizamos la función de normalización vista en labs anteriores
def normalize(text, remove_tildes = True):
    """Normaliza una cadena de texto convirtiéndo todo a minúsculas, quitando los caracteres no alfabéticos y los tildes"""
    text = text.lower() # Llevamos todo a minúscula
    text = re.sub(r'[^A-Za-zñáéíóú]', ' ', text) # Reemplazamos los caracteres no alfabéticos por un espacio
    if remove_tildes:
        text = re.sub('á', 'a', text) # Reemplazamos los tildes
        text = re.sub('é', 'e', text)
        text = re.sub('í', 'i', text)
        text = re.sub('ó', 'o', text)
        text = re.sub('ú', 'u', text)
    return text

In [5]:
spanish_diagnostics_normalized = spanish_diagnostics.map(
    lambda x: {
        "normalized_text" : normalize(x["text"])
    })

Map:   0%|          | 0/70000 [00:00<?, ? examples/s]

Map:   0%|          | 0/30000 [00:00<?, ? examples/s]

In [6]:
spanish_diagnostics_normalized_tokenized = spanish_diagnostics_normalized.map(
    lambda x: {
        "tokenized_text" : x["normalized_text"].split()
    })

Map:   0%|          | 0/70000 [00:00<?, ? examples/s]

Map:   0%|          | 0/30000 [00:00<?, ? examples/s]

## Word embeddings

Los word embeddings son representaciones vectoriales de palabras. A cada una de las palabras de nuestro vocabulario se les asigna un vector que la representa y estas representaciones guardan relaciones semánticas del lenguaje natural. Por ejemplo, palabras semánticamente similares tienen a estar más cerca en el espacio que palabras no tan similares entre sí.

Para calcular estas representaciones utilizaremos el método Word2Vec, en su implementación de la biblioteca Gensim.

Para calcular las representaciones, simplemente pasamos nuestro corpus tokenizado al objeto Word2Vec.

In [7]:
model = gensim.models.Word2Vec(spanish_diagnostics_normalized_tokenized["train"]["tokenized_text"])

Tenemos una representación de 100 dimensiones para cada una de las palabras del vocabulario.

In [8]:
model.wv.vectors.shape

(6316, 100)

Si extraemos el vector asociado a una palabra se observa que está constituido de números reales.

In [9]:
model.wv["pieza"]

array([-0.44924557, -1.5715238 ,  0.47973466, -0.7290032 , -0.7510085 ,
       -0.47328892, -2.2066853 ,  0.13899627, -0.32029143, -2.6607141 ,
        0.48708063,  1.6970999 , -1.4778588 , -0.02332565,  1.1997026 ,
        0.45629984, -1.5674058 , -1.7303785 , -0.24410908, -0.30030182,
       -1.397491  , -0.29266977,  0.8854643 ,  0.9414448 , -0.5267291 ,
        0.18488866, -0.43811864,  0.69757843,  0.561908  ,  0.7831236 ,
        0.36899424, -1.9946109 ,  1.3944435 , -0.39884272, -0.04372713,
        1.0277143 ,  0.28502947,  1.5267895 ,  0.8514398 ,  0.24174806,
        0.7916845 , -1.9216356 , -0.08104719, -0.01660866,  0.42291513,
       -0.17138568,  0.48716426, -0.03183713,  1.2323408 ,  0.88283557,
        0.08992244, -0.05722816,  0.06775829,  0.8657225 , -0.14191927,
       -1.1227683 , -0.67531496,  0.85729873, -0.9046628 , -0.7680791 ,
       -0.12288745,  1.3725915 ,  3.0286205 ,  0.19919343, -0.6136304 ,
        0.3465908 ,  1.3618324 , -0.08869272, -2.2555473 ,  0.40

Una de las métricas más utilizadas para establecer distancias entre vectores de palabras es la similaridad coseno, esta métrica está por defecto utilizada cuando deseamos saber las palabras más cercanas a un palabra que consultamos. Se observa que las palabras más cercanas a la palabra consultada guardan una estrecha relación semántica.

### Similaridad

In [10]:
model.wv.most_similar("pieza")

[('pza', 0.9343826174736023),
 ('pd', 0.8911149501800537),
 ('pz', 0.8599935173988342),
 ('diente', 0.799839973449707),
 ('dte', 0.7879177331924438),
 ('piezas', 0.783124566078186),
 ('pzas', 0.7679053544998169),
 ('radiograficamente', 0.7089167237281799),
 ('raices', 0.7036550641059875),
 ('mesioversion', 0.6909011006355286)]

Para continuar con la verificación de la similaridad de palabras establecemos pares de palabras en donde cada vez iremos alejándolas semánticamente. También podemos concluir que nuestro modelo pudo satisfactoriamente representar estas distancias de manera correcta.

In [39]:
pairs = [
    ('pieza', 'diente'), # Palabras muy cercanas semánticamente
    ('pieza', 'caries'),
    ('pieza', 'protesis'),
    ('pieza', 'hueso'),
    ('pieza', 'sangre') # Palabras muy lejanas semanticamente
]

In [12]:
for w1, w2 in pairs:
    print('%r\t%r\t%.2f' % (w1, w2, model.wv.similarity(w1, w2)))

'pieza'	'diente'	0.80
'pieza'	'caries'	0.57
'pieza'	'protesis'	0.28
'pieza'	'hueso'	0.19
'pieza'	'sangre'	0.11


Una de las aplicaciones de la similaridad de palabras es la detección de palabras fuera de contexto en una lista de palabras. En este caso el modelo detectó correctamente la palabra extraña.

In [13]:
model.wv.doesnt_match(["diente","periodontitis","cirrosis","corona","lengua"])

'cirrosis'

### Analogía

> Analogía, significa comparación o relación entre varias cosas, razones o conceptos; comparar o relacionar dos o más seres u objetos a través de la razón; señalando características generales y particulares comunes que permiten justificar la existencia de una propiedad en uno, a partir de la existencia de dicha propiedad en los otros.
>
>En el aspecto lógico, permite comparar un objeto con otros, en sus semejanzas y en sus diferencias. Una analogía permite la deducción de un término desconocido a partir del análisis de la relación que se establece entre dos términos conocidos.
>
> Analogía - Wikipedia

Tomando en cuenta esta definición podemos construir analogías como las siguientes:

* *pieza* es a *caries* como *ojo* es a *catarata*
* *bacteria* es a *antibiótico* como *virus* es a *antiviral*

Si a estos cuartetos de palabras le quitamos una, podemos transformar estas analogías en preguntas de analogía y esta es una tarea en la cual los word embeddings típicamente son probados:

* *pieza* es a *caries* como *ojo* es a *¿?*
* *bacteria* es a *antibiótico* como *virus* es a *¿?*

La relación vectorial que podemos construir para resolver estas pruebas es la siguiente:

Siendo $w_1$, $w_2$, $w_3$, $w_4$ los vectores asociados a las 4 palabras de la analogía, se cumple que $w_2 - w_1 	\approx w_4 - w_3$, por lo que para resolver una prueba de analogía, la posición de la palabra incógnita $w_4$ es $w_2 - w_1 + w_3$.

Aquí vemos como nuestro modelo resuelve correctamente una prueba de analogía.

In [14]:
w_1 = model.wv["pieza"]
w_2 = model.wv["caries"]
w_3 = model.wv["ojo"]
w_4 = w_2 - w_1 + w_3

model.wv.similar_by_vector(w_4)

[('catarata', 0.6485856771469116),
 ('ojo', 0.6401976943016052),
 ('pterigion', 0.6279850602149963),
 ('oi', 0.6259358525276184),
 ('cataratas', 0.6031419634819031),
 ('glaucoma', 0.5798618197441101),
 ('borrosa', 0.5558717846870422),
 ('snellen', 0.5556248426437378),
 ('amaurosis', 0.5457671284675598),
 ('estrabismo', 0.5454263687133789)]

También gensim implementa el método Word2Vec.most_similar() que nos ayuda a resolver en 1 línea esta operación.

In [15]:
model.wv.most_similar(positive=["caries", "ojo"], negative=["pieza"])

[('catarata', 0.7030323147773743),
 ('pterigion', 0.6931082606315613),
 ('oi', 0.6795079112052917),
 ('cataratas', 0.6582671403884888),
 ('glaucoma', 0.6553371548652649),
 ('amaurosis', 0.6269679665565491),
 ('borrosa', 0.6214637160301208),
 ('ocular', 0.6124424934387207),
 ('fondo', 0.6037007570266724),
 ('estrabismo', 0.603569746017456)]

### Visualización

Para poder visualizar nuestro espacio vectorial debemos proyectar los embeddings en 2 dimensiones, para lo cual utilizaremos un método de reducción de dimensionalidad

In [16]:
projector = sklearn.decomposition.PCA(3)
vectors_2d = projector.fit_transform(model.wv.vectors)[:,:2]

Podemos explorar en un espacio bidimensional las relaciones de cada una de nuestras palabras.

In [17]:
fig = px.scatter(
    x=vectors_2d[:,0],
    y=vectors_2d[:,1],
    text=model.wv.index_to_key
)
fig.update_traces(mode="markers")

### Comparación

Existen word embeddings precalculados disponibles libremente en internet. Utilizaremos como embedding de dominio general el Spanish Billion Words Corpus Embeddings y compararemos el rendimiento sobre pruebas clínicas de los 2 embeddings.

Cargamos los embeddings.

In [18]:
!curl -L -o sbwce_slim.txt https://raw.githubusercontent.com/dccuchile/CC66Q/main/tutorials/data/sbwce_slim.txt

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100 27.2M  100 27.2M    0     0  9674k      0  0:00:02  0:00:02 --:--:-- 9673k


In [19]:
sbwce = gensim.models.KeyedVectors.load_word2vec_format("sbwce_slim.txt")

Podemos observar que si probamos este modelo sobre palabras del dominio clínico, los resultados de estas pruebas son desfavorables.

In [20]:
sbwce.most_similar("pieza")

[('piezas', 0.6851319074630737),
 ('obra', 0.5722230672836304),
 ('cuerda', 0.5271234512329102),
 ('figura', 0.49860382080078125),
 ('máquina', 0.48856663703918457),
 ('elemento', 0.47292402386665344),
 ('clave', 0.47156471014022827),
 ('escultura', 0.46959367394447327),
 ('montaje', 0.46599438786506653),
 ('estructura', 0.4569995105266571)]

In [21]:
for w1, w2 in pairs:
    try:
        print('%r\t%r\t%.2f' % (w1, w2, sbwce.similarity(w1, w2)))
    except KeyError as e:
        print(e)

"Key 'diente' not present"
"Key 'caries' not present"
"Key 'protesis' not present"
"Key 'hueso' not present"
'pieza'	'sangre'	0.21


In [22]:
sbwce.doesnt_match(["diente","periodontitis","cirrosis","corona","lengua"])

'corona'

Probamos una analogía típica utilizada para verificar el rendimiento de los modelos de dominio general.

In [23]:
sbwce.most_similar(positive=["mujer", "rey"], negative=["hombre"], topn=3)

[('reina', 0.7493032217025757),
 ('princesa', 0.6861547231674194),
 ('reyes', 0.6391469836235046)]

In [24]:
sbwce_2d = projector.fit_transform(sbwce.vectors)[:,:2]

In [25]:
fig = px.scatter(
    x=sbwce_2d[:,0],
    y=sbwce_2d[:,1],
    text=list(sbwce.index_to_key)
)
fig.update_traces(mode="markers")

## Clasificación de textos

Definimos una función que nos retornará una representación de un documento desde representaciones de palabras.

In [26]:
def to_vector(tokens,model):
    """ Receives a sentence string along with a word embedding model and
    returns the vector representation of the sentence"""
    vec = np.zeros(model.vectors.shape[1]) # creates an empty vector of 300 dimensions
    for word in tokens: # iterates over the sentence
        if word in model: # checks if the word is in the word embedding
            vec += model[word] # adds every word embedding to the vector
    if np.linalg.norm(vec) > 0:
        return vec / np.linalg.norm(vec) # divides the vector by their normal
    else:
        return vec

Utilizaremos la función definida anteriormente para obtener la representación vectorial de cada uno de los ejemplos de nuestro conjunto de datos.

In [27]:
spanish_diagnostics_normalized_tokenized_vectorized = spanish_diagnostics_normalized_tokenized.map(
    lambda x: {
        "vectorized_text" : to_vector(x["tokenized_text"],model.wv)
    })

Map:   0%|          | 0/70000 [00:00<?, ? examples/s]

Map:   0%|          | 0/30000 [00:00<?, ? examples/s]

Exploramos el espacio y verificamos que existe una separación relativamente clara entre los documentos de las distintas clases.

In [57]:
def plot_3d(x, labels):
    """Generates a 3D scatter plot."""
    fig = px.scatter_3d(
        x=x[:, 0],
        y=x[:, 1],
        z=x[:, 2],
        color=labels,
        opacity=0.5
    )
    fig.update_traces(mode="markers", marker={'size': 2})
    fig.show()

In [59]:
examples_3d = projector.fit_transform(spanish_diagnostics_normalized_tokenized_vectorized["test"]["vectorized_text"])
labels = spanish_diagnostics_normalized_tokenized_vectorized["test"].features["label"].int2str(spanish_diagnostics_normalized_tokenized_vectorized["test"]["label"])

plot_3d(examples_3d , labels)

Instanciamos y ajustamos un modelo de regresión logística para clasificar nuestros textos y vemos que este método tiene un rendimiento significativamente bueno

In [50]:
classifier = sklearn.linear_model.LogisticRegression(solver='liblinear')

In [51]:
classifier.fit(
    spanish_diagnostics_normalized_tokenized_vectorized["train"]["vectorized_text"],
    spanish_diagnostics_normalized_tokenized_vectorized["train"]["label"]
)

LogisticRegression(solver='liblinear')

In [32]:
print(sklearn.metrics.classification_report(
    spanish_diagnostics_normalized_tokenized_vectorized["test"]["label"],
    classifier.predict(spanish_diagnostics_normalized_tokenized_vectorized["test"]["vectorized_text"])
))

              precision    recall  f1-score   support

           0       0.93      0.94      0.94     15034
           1       0.94      0.93      0.94     14966

    accuracy                           0.94     30000
   macro avg       0.94      0.94      0.94     30000
weighted avg       0.94      0.94      0.94     30000



### Comparación de Word Embeddings

Realizamos el mismo proceso de vectorización pero utilizando las representaciones de dominio general y verificamos que el rendimiento es mucho menor al anterior.

In [33]:
spanish_diagnostics_normalized_tokenized_vectorized_sbwce = spanish_diagnostics_normalized_tokenized.map(
    lambda x: {
        "vectorized_text" : to_vector(x["tokenized_text"],sbwce)
    })

Map:   0%|          | 0/70000 [00:00<?, ? examples/s]

Map:   0%|          | 0/30000 [00:00<?, ? examples/s]

In [60]:
examples_3d_sbwce = projector.fit_transform(spanish_diagnostics_normalized_tokenized_vectorized_sbwce["test"]["vectorized_text"])
labels = spanish_diagnostics_normalized_tokenized_vectorized["test"].features["label"].int2str(spanish_diagnostics_normalized_tokenized_vectorized["test"]["label"])

plot_3d(examples_3d_sbwce , labels)

In [36]:
classifier_sbwce = sklearn.linear_model.LogisticRegression(solver='liblinear')

In [37]:
classifier.fit(
    spanish_diagnostics_normalized_tokenized_vectorized_sbwce["train"]["vectorized_text"],
    spanish_diagnostics_normalized_tokenized_vectorized_sbwce["train"]["label"]
)

LogisticRegression(solver='liblinear')

In [38]:
print(sklearn.metrics.classification_report(
    spanish_diagnostics_normalized_tokenized_vectorized_sbwce["test"]["label"],
    classifier.predict(spanish_diagnostics_normalized_tokenized_vectorized_sbwce["test"]["vectorized_text"])
))

              precision    recall  f1-score   support

           0       0.76      0.90      0.82     15034
           1       0.87      0.72      0.79     14966

    accuracy                           0.81     30000
   macro avg       0.82      0.81      0.81     30000
weighted avg       0.82      0.81      0.81     30000

